In [1]:
import numpy as np
import gensim
import torch
import pandas as pd
import csv
import seaborn as sns
from sklearn.model_selection import train_test_split

from torchtext.vocab import Vocab
from collections import Counter

from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics import accuracy_score

C:\Users\p_ulanicki\anaconda3\lib\site-packages\gensim\similarities\__init__.py:15: UserWarning: The gensim.similarities.levenshtein submodule is disabled, because the optional Levenshtein package <https://pypi.org/project/python-Levenshtein/> is unavailable. Install Levenhstein (e.g. `pip install python-Levenshtein`) to suppress this warning.
  warnings.warn(msg)


In [2]:
train_set = pd.read_table('train/train.tsv', error_bad_lines=False, header=None, quoting=csv.QUOTE_NONE)

In [3]:
train_set

0  \
0    B-ORG O B-MISC O O O B-MISC O O O B-PER I-PER ...   
1    O B-PER O O O O O O O O O B-LOC O O O O O O O ...   
2    B-LOC O B-LOC O O O O O O B-LOC O O B-LOC O O ...   
3    B-LOC O O O O B-LOC O O O B-LOC O O B-LOC O O ...   
4    B-MISC O O O O O O O O O O O B-LOC O O B-MISC ...   
..                                                 ...   
940  O O B-PER O O O O O O O B-PER I-PER O B-LOC O ...   
941  O O O O O O O O B-LOC O B-LOC O O O O O O O O ...   
942  O O B-MISC O B-PER O B-ORG O O B-LOC O B-LOC O...   
943  O O B-LOC I-LOC B-MISC I-MISC O O O O B-LOC O ...   
944  O O B-MISC I-MISC O O O O O B-LOC O B-LOC O O ...   

                                                     1  
0    EU rejects German call to boycott British lamb...  
1    Rare Hendrix song draft sells for almost $ 17,...  
2    China says Taiwan spoils atmosphere for talks ...  
3    China says time right for Taiwan talks . </S> ...  
4    German July car registrations up 14.2 pct yr /...  
..                                                 ...  
940  CYCLING - BALLANGER KEEPS SPRINT TITLE IN STYL...  
941  CYCLING - WORLD TRACK CHAMPIONSHIP RESULTS . <...  
942  SOCCER - FRENCH DEFENDER KOMBOUARE JOINS ABERD...  
943  MOTORCYCLING - SAN MARINO GRAND PRIX PRACTICE ...  
944  GOLF - BRITISH MASTERS THIRD ROUND SCORES . </...  

[945 rows x 2 columns]

In [4]:
train = pd.read_table('train/train.tsv', error_bad_lines=False, header=None, quoting=csv.QUOTE_NONE)

def split(x):
    return x.split()

def replace(x):
    newList = []
    for word in x:
        if word == 'O':
            newList.append(0)
        if word == 'B-LOC':
            newList.append(1)
        if word == 'I-LOC':
            newList.append(2)
        if word == 'B-MISC':
            newList.append(3)
        if word == 'B-ORG':
            newList.append(4)
        if word == 'I-ORG':
            newList.append(5)
        if word == 'B-PER':
            newList.append(6)
        if word == 'I-PER':
            newList.append(7)
    return newList

train[0] = train[0].map(split)
train[1] = train[1].map(split)
train[0] = train[0].map(replace)

In [5]:
def build_vocab(dataset):
    counter = Counter()
    for document in dataset:
        counter.update(document)
    return Vocab(counter, specials=['<unk>', '<pad>', '<bos>', '<eos>'])

def labels_process(dt):
    return [ torch.tensor([0] + document + [0], dtype = torch.long) for document in dt]

def data_process(dt):
    return [ torch.tensor([vocab['<bos>']] +[vocab[token]  for token in  document ] + [vocab['<eos>']], dtype = torch.long) for document in dt]

In [6]:
class NeuralNetwork(torch.nn.Module):
    def __init__(self, output_size):
        super(NeuralNetwork, self).__init__()
        self.fc1 = torch.nn.Linear(10_000,len(train_tokens_ids))
        self.softmax = torch.nn.Softmax(dim=0)
        
    def forward(self, x):
        x = self.fc1(x)
        x = self.softmax(x)
        return x

    
class NERModel(torch.nn.Module):
    def __init__(self,):
        super(NERModel, self).__init__()
        self.emb = torch.nn.Embedding(23627,200)
        self.fc1 = torch.nn.Linear(600,9)

    def forward(self, x):
        x = self.emb(x)
        x = x.reshape(600) 
        x = self.fc1(x)
        return x

In [7]:
vocab = build_vocab(train[1])
train_labels = labels_process(train[0])
train_tokens_ids = data_process(train[1])

In [8]:
ner_model = NERModel()
criterion = torch.nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(ner_model.parameters())
nn_model = NeuralNetwork(len(train_tokens_ids))

In [9]:
train_tokens_ids

[tensor([    2,   967, 22410,   239,   774,    10,  4588,   213,  7687,     5,
             4,   740,  2091,     4,  1388,   138,     4,    22,   231,   460,
            17,    16,    70,    39, 10855,    28,   239,  4552,    10,  2621,
            10, 22766,   213,  7687,   425,  4100,  2178,   514,  1897,  2010,
           663,   295,    43, 11848,    10,  2056,     5,     4,   118,    18,
          3489,    10,     7,   231,   494,    18,  3107,  1089, 10434, 10494,
            17,    16,    75,  2621,   264,   893, 11638,    30,   547,   128,
           116,   126,   425,     7,  2717,  4552,    23, 19846,     5,     4,
            15,   121,   172,   202,   348,   217,   584,  7880,   159,   103,
           172,   202,   847,   217,  3987,    19,    39,     6,    15,     7,
           460,    18,   451,   179, 17516,  1380,  2632, 17769,    91,    11,
           241,  3909,     5,     4,    86,    17,   724,  2717,  2464,    23,
          3071,    14,   201,    39,    23,   340,  

In [10]:
for epoch in range(2):
    loss_score = 0
    acc_score = 0
    prec_score = 0
    selected_items = 0
    recall_score = 0
    relevant_items = 0
    items_total = 0
    nn_model.train()
    for i in range(100):
        for j in range(1, len(train_labels[i]) - 1):
            X = train_tokens_ids[i][j-1: j+2]
            Y = train_labels[i][j: j+1]
            
            Y_predictions = ner_model(X)
            
            acc_score += int(torch.argmax(Y_predictions) == Y)
            
            if torch.argmax(Y_predictions) != 0:
                selected_items +=1
            if  torch.argmax(Y_predictions) != 0 and torch.argmax(Y_predictions) == Y.item():
                prec_score += 1
            
            if  Y.item() != 0:
                relevant_items +=1
            if  Y.item() != 0 and torch.argmax(Y_predictions) == Y.item():
                recall_score += 1
                
            items_total += 1
            
            optimizer.zero_grad()
            loss = criterion(Y_predictions.unsqueeze(0), Y)
            loss.backward()
            optimizer.step()
            loss_score += loss.item() 

    
precision = prec_score / selected_items
recall = recall_score / relevant_items
f1_score = (2*precision * recall) / (precision + recall)
display('loss: ', loss_score / items_total)
display('acc: ', acc_score / items_total)
display('prec: ', precision)
display('recall: : ', recall)
display('f1: ', f1_score)

'loss: '

0.5651189693641464

'acc: '

0.860387657861868

'prec: '

0.5599708348523514

'recall: : '

0.4143512274076072

'f1: '

0.4762790697674419

In [11]:
dev_in = pd.read_table('dev-0/in.tsv', error_bad_lines=False, header=None, quoting=csv.QUOTE_NONE)
dev_ex = pd.read_table('dev-0/expected.tsv', error_bad_lines=False, header=None, quoting=csv.QUOTE_NONE)

In [12]:
dev_in[0] = dev_in[0].map(split)
dev_ex[0] = dev_ex[0].map(split)
dev_ex[0] = dev_ex[0].map(replace)

In [13]:
dev_ex[0]

0      [0, 0, 4, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, ...
1      [0, 0, 3, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, ...
2      [0, 0, 0, 3, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 3, ...
3      [0, 0, 6, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, ...
4      [0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, ...
                             ...                        
210    [1, 0, 6, 0, 1, 0, 6, 0, 0, 1, 0, 0, 3, 0, 0, ...
211    [0, 0, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 4, 5, ...
212    [0, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, ...
213    [0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 3, 0, ...
214    [0, 4, 0, 0, 0, 1, 0, 0, 0, 6, 7, 0, 0, 0, 1, ...
Name: 0, Length: 215, dtype: object

In [14]:
dev_labels = labels_process(dev_ex[0])
dev_tokens_ids = data_process(dev_in[0])

In [90]:
result = []
nn_model.eval()

for i in range(len(dev_tokens_ids)):
    result.append([])
    for j in range(1, len(dev_labels[i]) - 1):

        X = dev_tokens_ids[i][j-1: j+2]
        Y = dev_labels[i][j: j+1]

        Y_predictions = ner_model(X)
        
        loss = criterion(Y_predictions.unsqueeze(0), Y)
        
        result[i].append(int(torch.argmax(Y_predictions)))

In [91]:
def generate_result(result):
    features = ['O', 'B-LOC', 'I-LOC', 'B-MISC', 'B-ORG', 'I-ORG', 'B-PER', 'B-PER', 'I-PER']
    final_result = []
    
    for i in range(len(result)):
        final_result.append([])
        for j in range(len(result[i])):
            final_result[i].append(features[result[i][j]])
            
    f = open("dev-0/out.tsv", "a")
    for i in final_result:
        f.write(' '.join(i) + '\n')
    f.close()
    
generate_result(result)

In [92]:
test_in = pd.read_table('test-A/in.tsv', error_bad_lines=False, header=None, quoting=csv.QUOTE_NONE)
test_in[0] = test_in[0].map(split)
test_tokens_ids = data_process(test_in[0])

In [93]:
result_test = []
nn_model.eval()

for i in range(len(test_tokens_ids)):
    result_test.append([])
    for j in range(1, len(test_tokens_ids[i]) - 1):

        X = test_tokens_ids[i][j-1: j+2]
        Y_predictions = ner_model(X)

        loss = criterion(Y_predictions.unsqueeze(0), Y)
        
        result_test[i].append(int(torch.argmax(Y_predictions)))

In [94]:
def generate_result(result):
    features = ['O', 'B-LOC', 'I-LOC', 'B-MISC', 'B-ORG', 'I-ORG', 'B-PER', 'B-PER', 'I-PER']
    final_result = []
    
    for i in range(len(result)):
        final_result.append([])
        for j in range(len(result[i])):
            final_result[i].append(features[result[i][j]])
            
    f = open("test-A/out.tsv", "a")
    for i in final_result:
        f.write(' '.join(i) + '\n')
    f.close()
    
generate_result(result_test)